In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

g_year = 108
g_season = 1
g_how_many_year = 3

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True)#, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'公司代號'] != u'公司代號']
    df = df[~df[u'公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',u'公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on=u'公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_gross_profit_sii = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'sii', 'GrossProfitMargin', u'毛利率(%)(營業毛利)/(營業收入)', '營益分析彙總表')

df_gross_profit_sii

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



毛利率(%)(營業毛利)/(營業收入)
('year:', 107)
('season:', 4)
毛利率(%)(營業毛利)/(營業收入)
('year:', 107)
('season:', 3)
毛利率(%)(營業毛利)/(營業收入)
('year:', 107)
('season:', 2)
毛利率(%)(營業毛利)/(營業收入)
('year:', 107)
('season:', 1)
毛利率(%)(營業毛利)/(營業收入)
('year:', 106)
('season:', 4)
毛利率(%)(營業毛利)/(營業收入)
('year:', 106)
('season:', 3)
毛利率(%)(營業毛利)/(營業收入)
('year:', 106)
('season:', 2)
毛利率(%)(營業毛利)/(營業收入)
('year:', 106)
('season:', 1)
毛利率(%)(營業毛利)/(營業收入)
('year:', 105)
('season:', 4)
毛利率(%)(營業毛利)/(營業收入)
('year:', 105)
('season:', 3)
毛利率(%)(營業毛利)/(營業收入)
('year:', 105)
('season:', 2)
毛利率(%)(營業毛利)/(營業收入)
('year:', 105)
('season:', 1)


公司代號      公司名稱 GrossProfitMargin(%)_108Q1 GrossProfitMargin(%)_107Q4  \
0    1101        台泥                      25.59                      26.96   
1    1102        亞泥                      24.03                      25.59   
2    1103        嘉泥                      14.42                      13.79   
3    1104      環球水泥                       8.96                      11.94   
4    1108      幸福水泥                       3.20                       1.40   
5    1109      信大水泥                      28.62                      32.59   
6    1110        東泥                       8.38                       8.62   
7    1201      味全公司                      29.73                      31.07   
8    1203      味王公司                      31.21                      32.40   
9    1210      大成長城                      14.60                      13.93   
10   1215      卜蜂企業                      14.35                      13.46   
11   1216        統一                      34.42                      33.67   
12   1217       愛之味                      30.92                      31.94   
13   1218      泰山企業                      18.14                      18.12   
14   1219      福壽實業                       8.88                       6.75   
15   1220        台榮                      11.12                      12.28   
16   1225       福懋油                       9.82                       8.09   
17   1227        佳格                      30.47                      30.19   
18   1229      聯華實業                      16.38                      16.32   
19   1231      聯華食品                      20.94                      21.91   
20   1232       大統益                      13.65                      10.96   
21   1233        天仁                      58.84                      57.28   
22   1234        黑松                      20.81                      23.79   
23   1235        興泰                       1.90                      46.42   
24   1236      宏亞食品                      24.77                      26.71   
25   1256   鮮活果汁-KY                      35.96                      35.52   
26   1262     綠悅-KY                      -5.05                      -0.57   
27   1301        台塑                      15.37                      16.19   
28   1303      南亞塑膠                       9.20                      14.73   
29   1304        台聚                      11.56                       9.52   
30   1305        華夏                      13.90                      17.79   
31   1307      三芳化工                      20.17                      20.31   
32   1308        亞聚                      10.35                       4.46   
33   1309      台達化工                       8.55                       4.81   
34   1310        台苯                      15.26                      12.85   
35   1312      國喬石化                      13.81                      16.39   
36   1313        聯成                       1.58                       5.07   
37   1314       中石化                       3.78                      13.44   
38   1315      達新工業                      16.05                      15.02   
39   1316        上曜                      10.57                      29.33   
40   1319        東陽                      24.37                      22.87   
41   1321        大洋                       5.36                       3.91   
42   1323        永裕                      21.06                      23.80   
43   1324      地球工業                      14.66                      15.67   
44   1325        恒大                      11.35                      11.11   
45   1326        台化                      13.72                      13.13   
46   1337     再生-KY                     -25.46                     -53.00   
47   1338     廣華-KY                      25.59                      24.49   
48   1339        昭輝                      25.18                      26.16   
49   1340     勝悅-KY                      -5.56                      16.86   
50   1402       遠東新                      17.56                      19.42   
5

In [5]:
df_gross_profit_otc = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'otc', 'GrossProfitMargin', u'毛利率(%)(營業毛利)/(營業收入)', '營益分析彙總表')

df_gross_profit_otc

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



毛利率(%)(營業毛利)/(營業收入)
('year:', 107)
('season:', 4)
毛利率(%)(營業毛利)/(營業收入)
('year:', 107)
('season:', 3)
毛利率(%)(營業毛利)/(營業收入)
('year:', 107)
('season:', 2)
毛利率(%)(營業毛利)/(營業收入)
('year:', 107)
('season:', 1)
毛利率(%)(營業毛利)/(營業收入)
('year:', 106)
('season:', 4)
毛利率(%)(營業毛利)/(營業收入)
('year:', 106)
('season:', 3)
毛利率(%)(營業毛利)/(營業收入)
('year:', 106)
('season:', 2)
毛利率(%)(營業毛利)/(營業收入)
('year:', 106)
('season:', 1)
毛利率(%)(營業毛利)/(營業收入)
('year:', 105)
('season:', 4)
毛利率(%)(營業毛利)/(營業收入)
('year:', 105)
('season:', 3)
毛利率(%)(營業毛利)/(營業收入)
('year:', 105)
('season:', 2)
毛利率(%)(營業毛利)/(營業收入)
('year:', 105)
('season:', 1)


公司代號    公司名稱 GrossProfitMargin(%)_108Q1 GrossProfitMargin(%)_107Q4  \
0    1258   其祥-KY                      14.61                      11.81   
1    1259      安心                      24.61                      25.84   
2    1264      德麥                      36.49                      37.04   
3    1333     恩得利                      27.82                      16.21   
4    1336      台翰                      12.49                      15.43   
5    1565    精華光學                      36.16                      37.39   
6    1566      捷邦                      14.51                      14.01   
7    1569      濱川                      17.69                      19.05   
8    1570    力肯實業                      21.82                      26.30   
9    1580    新麥企業                      41.75                      39.85   
10   1584    精剛精密                       1.56                       1.19   
11   1586    和勤精機                       8.01                      18.64   
12   1591   駿吉-KY                      13.32                      15.55   
13   1593      祺驊                      29.88                      30.75   
14   1595    川寶科技                      28.75                      30.31   
15   1597      直得                      44.09                      47.54   
16   1599     宏佳騰                      24.61                      24.55   
17   1742      台蠟                      10.83                      -7.50   
18   1752      南光                      30.43                      32.47   
19   1777      生泰                      35.21                      31.96   
20   1781    合世生醫                       9.38                      10.08   
21   1784    訊聯生技                      57.45                      57.49   
22   1785     光洋科                      14.58                      10.76   
23   1787     福盈科                      32.50                      32.12   
24   1788    杏昌生技                      22.81                      22.10   
25   1795    美時製藥                      49.44                      48.83   
26   1799      易威                      16.79                      12.09   
27   1813     寶利徠                      20.82                      14.35   
28   1815    富喬工業                      23.18                      27.24   
29   2035    唐榮公司                      -1.94                      -7.12   
30   2061      風青                       4.62                       4.08   
31   2063      世鎧                      32.43                      31.21   
32   2064      晉椿                       2.28                       7.76   
33   2066      世德                      27.64                      24.72   
34   2067      嘉鋼                      12.01                      19.25   
35   2221    大甲永和                      24.59                      27.42   
36   2230      泰茂                      16.01                      17.62   
37   2233      宇隆                      35.43                      37.66   
38   2235      謚源                      25.36                      23.26   
39   2596    綠意開發                      67.85                      43.26   
40   2640     大車隊                      48.95                      45.19   
41   2641    正德海運                      25.94                      25.89   
42   2643      捷迅                      11.17                      10.39   
43   2718      晶悅                      14.04                       4.79   
44   2719     燦星旅                      15.45                      12.15   
45   2724   富驛-KY                      11.79                       6.50   
46   2726   雅茗-KY                      53.09                      52.36   
47   2729    瓦城泰統                      54.30                      53.85   
48   2732    六角國際                      47.61                      47.49   
49   2734     易飛網                      22.98                      16.85   
50   2736      高野                      52.97                      48.29   
51   2740      天蔥                      34.57                      45.37   
52   2916    滿心企業             

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_gross_profit = pd.concat([df_gross_profit_sii,df_gross_profit_otc],axis=0, ignore_index=True)

df_gross_profit

公司代號      公司名稱 GrossProfitMargin(%)_108Q1 GrossProfitMargin(%)_107Q4  \
0     1101        台泥                      25.59                      26.96   
1     1102        亞泥                      24.03                      25.59   
2     1103        嘉泥                      14.42                      13.79   
3     1104      環球水泥                       8.96                      11.94   
4     1108      幸福水泥                       3.20                       1.40   
5     1109      信大水泥                      28.62                      32.59   
6     1110        東泥                       8.38                       8.62   
7     1201      味全公司                      29.73                      31.07   
8     1203      味王公司                      31.21                      32.40   
9     1210      大成長城                      14.60                      13.93   
10    1215      卜蜂企業                      14.35                      13.46   
11    1216        統一                      34.42                      33.67   
12    1217       愛之味                      30.92                      31.94   
13    1218      泰山企業                      18.14                      18.12   
14    1219      福壽實業                       8.88                       6.75   
15    1220        台榮                      11.12                      12.28   
16    1225       福懋油                       9.82                       8.09   
17    1227        佳格                      30.47                      30.19   
18    1229      聯華實業                      16.38                      16.32   
19    1231      聯華食品                      20.94                      21.91   
20    1232       大統益                      13.65                      10.96   
21    1233        天仁                      58.84                      57.28   
22    1234        黑松                      20.81                      23.79   
23    1235        興泰                       1.90                      46.42   
24    1236      宏亞食品                      24.77                      26.71   
25    1256   鮮活果汁-KY                      35.96                      35.52   
26    1262     綠悅-KY                      -5.05                      -0.57   
27    1301        台塑                      15.37                      16.19   
28    1303      南亞塑膠                       9.20                      14.73   
29    1304        台聚                      11.56                       9.52   
30    1305        華夏                      13.90                      17.79   
31    1307      三芳化工                      20.17                      20.31   
32    1308        亞聚                      10.35                       4.46   
33    1309      台達化工                       8.55                       4.81   
34    1310        台苯                      15.26                      12.85   
35    1312      國喬石化                      13.81                      16.39   
36    1313        聯成                       1.58                       5.07   
37    1314       中石化                       3.78                      13.44   
38    1315      達新工業                      16.05                      15.02   
39    1316        上曜                      10.57                      29.33   
40    1319        東陽                      24.37                      22.87   
41    1321        大洋                       5.36                       3.91   
42    1323        永裕                      21.06                      23.80   
43    1324      地球工業                      14.66                      15.67   
44    1325        恒大                      11.35                      11.11   
45    1326        台化                      13.72                      13.13   
46    1337     再生-KY                     -25.46                     -53.00   
47    1338     廣華-KY                      25.59                      24.49   
48    1339        昭輝                      25.18                      26.16   
49    1340     勝悅-KY                      -5.56                      16.86   
50    1402       遠東新        

In [7]:
#檢查column資料型態

#df_gross_profit.info() #non-null object
#df_gross_profit.dtypes #object
#df_gross_profit.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
GrossProfit(%)_107Q1    float64
GrossProfit(%)_106Q4    float64
GrossProfit(%)_106Q3    float64
GrossProfit(%)_106Q2    float64
GrossProfit(%)_106Q1    float64
GrossProfit(%)_105Q4    float64
GrossProfit(%)_105Q3    float64
GrossProfit(%)_105Q2    float64
GrossProfit(%)_105Q1    float64
GrossProfit(%)_104Q4    float64
GrossProfit(%)_104Q3    float64
GrossProfit(%)_104Q2    float64
GrossProfit(%)_104Q1    float64
dtype: object
'''

df_gross_profit = df_gross_profit.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_gross_profit.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                            int64
公司名稱                           object
GrossProfitMargin(%)_108Q1    float64
GrossProfitMargin(%)_107Q4    float64
GrossProfitMargin(%)_107Q3    float64
GrossProfitMargin(%)_107Q2    float64
GrossProfitMargin(%)_107Q1    float64
GrossProfitMargin(%)_106Q4    float64
GrossProfitMargin(%)_106Q3    float64
GrossProfitMargin(%)_106Q2    float64
GrossProfitMargin(%)_106Q1    float64
GrossProfitMargin(%)_105Q4    float64
GrossProfitMargin(%)_105Q3    float64
GrossProfitMargin(%)_105Q2    float64
GrossProfitMargin(%)_105Q1    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfitMargin(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['GrossProfitMargin(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['GrossProfitMargin(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfitMargin(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_gross_profit['Growth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_gross_profit['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True)#, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'有價證券代號及名稱'] != u'股票']
    df = df[~df[u'有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df[u'產業別'] > '0']
    del newdf[u'國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf[u'備註']

    df2=newdf[u'有價證券代號及名稱'].str.split(u' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if u'　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split(u'　')[1]
            df2.iat[i,0]=df2.iat[i,0].split(u'　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:u'公司代號',1:u'股票名稱'})
    del newdf[u'有價證券代號及名稱']

    return newdf

In [14]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_gross_profit = df_gross_profit.merge(df_basicinfo, on=u'公司代號', how='inner')

df_gross_profit

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號      公司名稱  GrossProfitMargin(%)_108Q1  GrossProfitMargin(%)_107Q4  \
0     1101        台泥                       25.59                       26.96   
1     1102        亞泥                       24.03                       25.59   
2     1103        嘉泥                       14.42                       13.79   
3     1104      環球水泥                        8.96                       11.94   
4     1108      幸福水泥                        3.20                        1.40   
5     1109      信大水泥                       28.62                       32.59   
6     1110        東泥                        8.38                        8.62   
7     1201      味全公司                       29.73                       31.07   
8     1203      味王公司                       31.21                       32.40   
9     1210      大成長城                       14.60                       13.93   
10    1215      卜蜂企業                       14.35                       13.46   
11    1216        統一                       34.42                       33.67   
12    1217       愛之味                       30.92                       31.94   
13    1218      泰山企業                       18.14                       18.12   
14    1219      福壽實業                        8.88                        6.75   
15    1220        台榮                       11.12                       12.28   
16    1225       福懋油                        9.82                        8.09   
17    1227        佳格                       30.47                       30.19   
18    1229      聯華實業                       16.38                       16.32   
19    1231      聯華食品                       20.94                       21.91   
20    1232       大統益                       13.65                       10.96   
21    1233        天仁                       58.84                       57.28   
22    1234        黑松                       20.81                       23.79   
23    1235        興泰                        1.90                       46.42   
24    1236      宏亞食品                       24.77                       26.71   
25    1256   鮮活果汁-KY                       35.96                       35.52   
26    1262     綠悅-KY                       -5.05                       -0.57   
27    1301        台塑                       15.37                       16.19   
28    1303      南亞塑膠                        9.20                       14.73   
29    1304        台聚                       11.56                        9.52   
30    1305        華夏                       13.90                       17.79   
31    1307      三芳化工                       20.17                       20.31   
32    1308        亞聚                       10.35                        4.46   
33    1309      台達化工                        8.55                        4.81   
34    1310        台苯                       15.26                       12.85   
35    1312      國喬石化                       13.81                       16.39   
36    1313        聯成                        1.58                        5.07   
37    1314       中石化                        3.78                       13.44   
38    1315      達新工業                       16.05                       15.02   
39    1316        上曜                       10.57                       29.33   
40    1319        東陽                       24.37                       22.87   
41    1321        大洋                        5.36                        3.91   
42    1323        永裕                       21.06                       23.80   
43    1324      地球工業                       14.66                       15.67   
44    1325        恒大                       11.35                       11.11   
45    1326        台化                       13.72                       13.13   
46    1337     再生-KY                      -25.46                      -53.00   
47    1338     廣華-KY                       25.59                       24.49   
48    1339        昭輝                       25.18                       26.16   
49    

In [15]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

"""
Export to Excel
Some support is available for exporting styled DataFrames to Excel worksheets using the OpenPyXL or XlsxWriter engines. 
CSS2.2 properties handled include:

* background-color
* border-style, border-width, border-color and their {top, right, bottom, left variants}
* color
* font-family
* font-style
* font-weight
* text-align
* text-decoration
* vertical-align
* white-space: nowrap
"""
def font_family(val):    
    fontfamily = 'Calibri'
    return 'font-family: %s' % fontfamily

def font_size(val):    
    fontsize = '10pt'
    return 'font-size: %s' % fontsize

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_gross_profit.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).applymap(font_family).applymap(font_size).to_excel('Styled_Basic_Perspective_GrossProfitMargin.xlsx', 'GrossProfitMargin_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_108Q1', '2QMAGrowth_108Q1', 'Growth_107Q4', '2QMAGrowth_107Q4', 'Growth_107Q3', '2QMAGrowth_107Q3', 'Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2']


C:\ProgramData\Anaconda2\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
